# GPT2-Small Resid Pre

In [11]:
import sys 
sys.path.append("../..")
sys.path.append("..")

from importlib import reload
from tqdm import tqdm

import joseph
from joseph.analysis import *
from joseph.visualisation import *
from joseph.utils import *
from joseph.data import *


reload(joseph.analysis)
reload(joseph.visualisation)
reload(joseph.utils)
reload(joseph.data)

from joseph.analysis import *
from joseph.visualisation import *
from joseph.utils import *
from joseph.data import *

# turn torch grad tracking off
torch.set_grad_enabled(False)

In [2]:

model = HookedTransformer.from_pretrained(
    "gpt2-small",
    # "tiny-stories-2L-33M",
    # "attn-only-2l",
    # center_unembed=True,
    # center_writing_weights=True,
    # fold_ln=True,
    # refactor_factored_attn_matrices=True,
)
model.set_use_split_qkv_input(True)
model.set_use_attn_result(True)


path = "../checkpoints/kdwz3z61/100003840_sparse_autoencoder_gpt2-small_blocks.10.hook_resid_pre_49152.pt"
sparse_autoencoder = SparseAutoencoder.load_from_pretrained(path)

print(sparse_autoencoder.cfg)


# sanity check
text = "Many important transition points in the history of science have been moments when science 'zoomed in.' At these points, we develop a visualization or tool that allows us to see the world in a new level of detail, and a new field of science develops to study the world through this lens."
model(text, return_type="loss")

Loaded pretrained model gpt2-small into HookedTransformer
LanguageModelSAERunnerConfig(model_name='gpt2-small', hook_point='blocks.10.hook_resid_pre', hook_point_layer=10, hook_point_head_index=None, dataset_path='Skylion007/openwebtext', is_dataset_tokenized=False, context_size=128, use_cached_activations=False, cached_activations_path='activations/Skylion007_openwebtext/gpt2-small/blocks.10.hook_resid_pre', d_in=768, n_batches_in_buffer=128, total_training_tokens=500000000, store_batch_size=32, device='mps', seed=42, dtype=torch.float32, expansion_factor=64, from_pretrained_path=None, l1_coefficient=0.00016, lr=0.0012, lr_scheduler_name=None, lr_warm_up_steps=500, train_batch_size=4096, feature_sampling_window=5000, feature_sampling_method='anthropic', resample_batches=128, feature_reinit_scale=0.2, dead_feature_window=20000, dead_feature_threshold=1e-06, log_to_wandb=True, wandb_project='mats_sae_training_gpt2_small_resid_pre', wandb_entity=None, wandb_log_frequency=100, n_checkpoin

tensor(3.3225, device='mps:0')

In [101]:
random_tokens, random_token_groups = generate_random_token_prompt(model, n_random_tokens=5, n_repeat_tokens=2)
prompt = model.to_string(random_tokens)
token_df, original_cache, cache_reconstructed_query, feature_acts = eval_prompt([prompt], model, sparse_autoencoder, head_idx_override=7)
print(token_df.columns)
filter_cols = ["str_tokens", "unique_token", "context", "batch", "pos", "label", "loss", "loss_diff", "mse_loss", "num_active_features", "explained_variance", "kl_divergence"]
token_df[filter_cols].tail(10).style.background_gradient(
    subset=["loss_diff", "mse_loss","explained_variance", "num_active_features", "kl_divergence"],
    cmap="coolwarm",
)

Index(['str_tokens', 'unique_token', 'context', 'batch', 'pos', 'label',
       'loss', 'max_idx_pos', 'max_idx_tok', 'max_idx_tok_value',
       'top10_token_suppression_diffs', 'top10_token_suppression_inds',
       'top10_token_boosting_vals', 'top10_token_boosting_inds',
       'ablated_loss', 'loss_diff', 'mse_loss', 'explained_variance',
       'num_active_features', 'top_k_feature_acts', 'top_k_features',
       'rec_q_max_idx_pos', 'rec_q_max_idx_tok', 'rec_q_max_idx_tok_value',
       'kl_divergence'],
      dtype='object')


In [102]:
HEAD_IDX = 7
LAYER_IDX = sparse_autoencoder.cfg.hook_point_layer
patterns_original = original_cache[utils.get_act_name("attn_scores", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
patterns_reconstructed = cache_reconstructed_query[utils.get_act_name("attn_scores", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
both_patterns = torch.stack([patterns_original, patterns_reconstructed])
plot_attn(both_patterns.detach().cpu(), token_df, title="Original and Reconstructed Attention Distribution")
patterns_original = original_cache[utils.get_act_name("pattern", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
patterns_reconstructed = cache_reconstructed_query[utils.get_act_name("pattern", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
both_patterns = torch.stack([patterns_original, patterns_reconstructed])
plot_attn(both_patterns.detach().cpu(), token_df, title="Original and Reconstructed Attention Distribution")

In [105]:
POS_INTEREST = feature_acts.shape[0] - 1 # index from 0.

# reload(joseph.visualisation)
# from joseph.visualisation import *

print(token_df["unique_token"][POS_INTEREST]) # bos gone.
plot_line_with_top_10_labels(feature_acts[POS_INTEREST], "", 10)

vals, inds = torch.topk(feature_acts[POS_INTEREST],5)

print(inds)
# plot_attn_score_by_feature(model, sparse_autoencoder, inds, original_cache, token_df, pos_interest=POS_INTEREST, vals = vals)
# plot_unembed_score_by_feature(model, sparse_autoencoder, inds, token_df, vals=vals)

 211/11


tensor([14106, 35103, 47594, 25215, 33522], device='mps:0')


In [110]:
# set pandas columns allowed to be as wide as they want.
pd.set_option('display.max_colwidth', None)
filter_columns = ["str_tokens", "unique_token", "context", "batch", "pos", "label", "loss", "loss_diff", "mse_loss", "num_active_features", "explained_variance", "kl_divergence"]
# features = torch.randint(0, sparse_autoencoder.cfg.d_sae, (50,))
# features = torch.tensor([24519,22818,31246])
for feature in inds:
    all_token_df[f"feature_{feature}"] = all_token_features[:,feature].detach().cpu()
    mean_activation = (all_token_df[f"feature_{feature}"] > 0).mean()
    if mean_activation > 0.001:
        print(feature.item(), (all_token_df[f"feature_{feature}"] > 0).mean()) # super super dense feature.
        display(all_token_df.sort_values(f"feature_{feature}", ascending=False)[filter_columns + [f"feature_{feature}"]].head(10))

14106 0.0029721696838692245


str_tokens unique_token                                                                       context  batch  pos  label      loss  loss_diff    mse_loss  num_active_features  explained_variance  kl_divergence  feature_14106
81         FRE       FRE/81                   Hayworth, FRE Photo: Justin Hayworth,| FRE| Image 1 of / 25      0   81   0/81  0.018759   0.001750   46.607876                   13            0.330087       0.143109      21.980942
16       Dirty     Dirty/16                Dirty Laundry short. Bernthal loves the| Dirty| Laundry short.      0   16   0/16  0.000176  -0.000004   44.717175                   20            0.256914       0.125043      11.745908
127          1        1/127                                       /2 c.cocoa powder\n\n|1|/2 c confection      0  127  0/127  1.247595   0.059816   26.610203                   14            0.190596       0.564326       6.287418
119    Michael  Michael/119             show that was the subject of his film ��|Michael| Moore in Trumpl      0  119  0/119  3.983482   0.354897   36.893539                   20            0.339095       0.792571       2.274184
34           s         s/34                     up.\n\nShe ended Friday night��|s| game with a simple rim      0   34   0/34  0.024406   0.004653   33.481567                   18            0.358172       0.465149       2.115583
74         The       The/74   a columnist at the Washington Examiner and author of "|The| Big Ripoff" and      0   74   0/74  1.285674  -0.070147   24.689127                   16            0.286941       0.152916       1.499258
65         and       and/65                         Hedwig and the Angry Inch��| and| ��Spring Awakening,      0   65   0/65  1.390135  -0.116342   24.993301                   13            0.271648       0.252346       1.136768
64           2         2/64                    \n\nA reference to Source 2 in the Dota| 2| mod tools.\n\n      0   64   0/64  0.149390  -0.048646   37.062008                   18            0.286754       0.585937       1.052479
50           2         2/50                  a new game," wrote RoyAwesome on the Dota| 2| subReddit.\n\n      0   50   0/50  0.144232  -0.018869   44.032204                   22            0.302668       0.875377       0.815591
94        with      with/94         of / 25 Caption Close Texans' attitudes shifting along| with| U.S. on      0   94   0/94  0.002861   0.000478  109.793884                   17            0.735938       0.929145       0.795748

35103 0.0018913807079167792


str_tokens  unique_token                                                                      context  batch  pos  label      loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_35103
112       milk      milk/112                    15g extra granulated sugar\n\n225g| milk| chocolate\n\n1/      0  112  0/112  3.679356   0.166413  40.817398                   17            0.361623       1.156627       4.085305
74           g          g/74                              Dragees\n\nIngredients:\n\n190|g| hazelnuts, to      0   74   0/74  1.175876   0.037893  38.982685                   18            0.363265       1.342930       2.074207
99       water      water/99                            \n20g unsalted butter\n\n10g| water|\n\n15g extra      0   99   0/99  4.412343   0.219823  27.495430                   14            0.316259       0.394536       1.509597
3         City        City/3                        1929 Vatican| City| postage stamp featuring the image      0    3    0/3  3.193809  -0.030002  25.921133                   25            0.318534       0.189247       0.915858
87       sugar      sugar/87                           nuts, toasted\n\n50g granulated| sugar|\n\n20g uns      0   87   0/87  0.113922   0.014641  35.349037                   13            0.408424       0.194798       0.733019
107      sugar     sugar/107                       10g water\n\n15g extra granulated| sugar|\n\n225g milk      0  107  0/107  0.039627  -0.021140  33.046909                   15            0.327734       0.442137       0.358500
83    pressure   pressure/83   (but are not limited to): rise in blood| pressure|, feeling as though your      0   83   0/83  0.090269  -0.001786  29.620352                   21            0.308501       0.341090       0.296064
123        fed       fed/123                  .[1] She was so small that she was| fed| with an eyedropper      0  123  0/123  7.142970  -0.106173  47.238525                   21            0.391877       0.754918       0.000000
125         an        an/125           ] She was so small that she was fed with| an| eyedropper until she      0  125  0/125  4.219623  -0.050569  32.067768                   54            0.311582       0.644384       0.000000
124       with      with/124              1] She was so small that she was fed| with| an eyedropper until      0  124  0/124  4.920561  -0.010869  24.544930                   23            0.264945       0.702756       0.000000

47594 0.012969467711429343


str_tokens unique_token                                                                                 context  batch  pos  label       loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_47594
81         FRE       FRE/81                             Hayworth, FRE Photo: Justin Hayworth,| FRE| Image 1 of / 25      0   81   0/81   0.018759   0.001750  46.607876                   13            0.330087       0.143109      79.719933
36          .)        .)/36                                        blue). (Image by Dr. Lucky Tran|.)|\n\nNEW YORK,      0   36   0/36   4.130130   0.084393  29.305809                   15            0.356718       0.456711      50.764606
75       Photo     Photo/75              federal involvement. Photo: Justin Hayworth, FRE| Photo|: Justin Hayworth,      0   75   0/75   8.459044   0.004910  34.276226                    8            0.426018       0.027333      38.778404
67           .         ./67   rape appear to be about his aversion to federal involvement|.| Photo: Justin Hayworth      0   67   0/67   0.009066  -0.000302  27.214043                   22            0.280045       0.233184      36.917816
104         25       25/104                                with U.S. on legalizing pot 1 /| 25| Back to Gallery\n\n      0  104  0/104   0.003839   0.000829  86.140015                   26            0.619284       2.095739      32.941257
21           .         ./21                             . Bernthal loves the Dirty Laundry short|.|\n\nThomas Jane�      0   21   0/21   0.000874   0.000018  56.664211                   13            0.456645       0.417939      30.706764
101        pot      pot/101                   attitudes shifting along with U.S. on legalizing| pot| 1 / 25 Back to      0  101  0/101   0.109918   0.004140  61.105507                   16            0.436796       0.503576      28.947393
31           .         ./31      courtesy of the Photo Collection, Los Angeles Public Library|.|\n\nNow fifty years      0   31   0/31   0.667827   0.004473  25.641462                   17            0.296444       0.385927      26.738356
82       Image     Image/82                        worth, FRE Photo: Justin Hayworth, FRE| Image| 1 of / 25 Caption      0   82   0/82   0.021765   0.012875  52.693493                   12            0.510352       0.226724      24.283340
86          25        25/86                : Justin Hayworth, FRE Image 1 of /| 25| Caption Close Texans' attitudes      0   86   0/86  10.243133   0.255642  67.995720                   17            0.620486       0.698797      23.719921

25215 0.021075385031072685


str_tokens  unique_token                                                                              context  batch  pos label      loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_25215
20          ,          ,/20         ine, circa 1952. Photo by Leonard Nadel| ,| courtesy of the Photo Collection      0   20  0/20  7.304225  -0.018623  22.483578                   18            0.278420       0.685245      21.610744
26          ,          ,/26   by Leonard Nadel , courtesy of the Photo Collection|,| Los Angeles Public Library.      0   26  0/26  2.727155   0.012064  23.089100                   26            0.310732       0.559960      21.587067
31          .          ./31   courtesy of the Photo Collection, Los Angeles Public Library|.|\n\nNow fifty years      0   31  0/31  0.667827   0.004473  25.641462                   17            0.296444       0.385927      19.645010
22         of         of/22         circa 1952. Photo by Leonard Nadel , courtesy| of| the Photo Collection, Los      0   22  0/22  0.193771  -0.022092  17.906260                   38            0.215241       0.050055      16.863682
6           :           :/6                                      China��s Military Blueprint|:| Bigger Navy, Big      0    6   0/6  3.353280  -0.056767  18.222147                   23            0.205079       0.156856      16.104250
14          .          ./14              of the community of Chavez Ravine, circa 1952|.| Photo by Leonard Nadel      0   14  0/14  0.295135  -0.008109  11.801653                   15            0.174343       0.121874      15.879065
12      circa      circa/12          amic view of the community of Chavez Ravine,| circa| 1952. Photo by Leonard      0   12  0/12  6.386649   0.128922  28.640770                   24            0.251943       0.205377      15.736553
3           (           (/3                                                 Felicia Pearson| (|born May 18, 1980      0    3   0/3  3.310565  -0.042509  10.906702                   15            0.154774       0.032021      12.464931
23        the        the/23       1952. Photo by Leonard Nadel , courtesy of| the| Photo Collection, Los Angeles      0   23  0/23  1.469165  -0.062362  15.563864                   28            0.190749       0.143758      12.375582
21   courtesy   courtesy/21           , circa 1952. Photo by Leonard Nadel ,| courtesy| of the Photo Collection,      0   21  0/21  2.370469  -0.008746  24.240894                   18            0.255724       0.280225      12.252549

33522 0.0761956228046474


str_tokens  unique_token                                                                                context  batch  pos label      loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_33522
14       ones       ones/14                  stay safe, protect & defend yourself & your loved| ones|.\n\nWe offer      0   14  0/14  0.045750   0.007838  27.848068                   25            0.333543       0.606411      21.703913
30    Library    Library/30         , courtesy of the Photo Collection, Los Angeles Public| Library|.\n\nNow fifty      0   30  0/30  0.056732   0.000271  34.070461                   21            0.362207       0.902953      21.550455
14       Role       Role/14                Military Blueprint: Bigger Navy, Bigger Global| Role|\n\nChina laid out      0   14  0/14  6.668837  -0.091453  23.628159                   30            0.234629       1.039828      21.344328
13       them       them/13                  addicting once you start you can not stop eating| them|.\n\nFirst you      0   13  0/13  1.869246  -0.046328  15.880016                   16            0.222112       0.136588      20.824211
13       down       down/13      health care is a powerful tool for keeping medical costs| down|. Contraception is      0   13  0/13  0.476577   0.031609  14.969417                   21            0.185825       0.056066      20.596983
13         XI         XI/13           City postage stamp featuring the image of Pope Pius| XI|\n\nThe Vatican post      0   13  0/13  2.471250   0.002036  18.818083                   25            0.181546       0.252592      19.529331
9      cooked      cooked/9                            Turns out the Pot Roast was under|cooked|.\n\nLong believed      0    9   0/9  3.124946   0.279686  22.011551                   29            0.255121       0.133490      19.479961
16      cover      cover/16                            do, so much to say, so much to| cover|. Starting with this:      0   16  0/16  8.735490   0.053012  33.241325                   30            0.435707       0.187089      19.372578
13       1952       1952/13               view of the community of Chavez Ravine, circa| 1952|. Photo by Leonard N      0   13  0/13  5.688097   0.029393  17.977463                   16            0.262942       0.169791      18.255850
37   property   property/37   were arrested when they refused to leave Dick Cheney's| property|\n\nWashington (CNN      0   37  0/37  4.146715  -0.072471  34.138554                   22            0.400429       0.509124      17.961655

In [21]:
data = get_webtext()

In [75]:
str_token_list = []
loss_list = []
ablated_loss_list = []
# data = get_webtext()

NUM_PROMPTS = 30
# MAX_PROMPT_LEN = 100
# BATCH_SIZE = 10
dataframe_list = []
feature_acts_list = []
with torch.no_grad():
    for i in tqdm(range(NUM_PROMPTS)):
        
        # Get Token Data
        prompt = data[i]
        # new_str = data[BATCH_SIZE * i: BATCH_SIZE * (i + 1)]
        

        token_df, _, _, feature_acts = eval_prompt(prompt, model, sparse_autoencoder, head_idx_override=7)
        feature_acts_list.append(feature_acts)
        dataframe_list.append(token_df)
        
all_token_df = pd.concat(dataframe_list)
all_token_df.reset_index(drop=True)
all_token_features = torch.cat(feature_acts_list)

print(all_token_df.shape)
print(all_token_df.columns)
all_token_df.head()

100%|██████████| 30/30 [04:02<00:00,  8.09s/it]

(22266, 25)
Index(['str_tokens', 'unique_token', 'context', 'batch', 'pos', 'label',
       'loss', 'max_idx_pos', 'max_idx_tok', 'max_idx_tok_value',
       'top10_token_suppression_diffs', 'top10_token_suppression_inds',
       'top10_token_boosting_vals', 'top10_token_boosting_inds',
       'ablated_loss', 'loss_diff', 'mse_loss', 'explained_variance',
       'num_active_features', 'top_k_feature_acts', 'top_k_features',
       'rec_q_max_idx_pos', 'rec_q_max_idx_tok', 'rec_q_max_idx_tok_value',
       'kl_divergence'],
      dtype='object')


str_tokens unique_token                             context  batch  pos  \
0        HOU        HOU/0              |HOU|STON — So much to      0    0   
1       STON       STON/1           HOU|STON| — So much to do      0    1   
2          —          —/2          HOUSTON| —| So much to do,      0    2   
3         So         So/3       HOUSTON —| So| much to do, so      0    3   
4       much       much/4  HOUSTON — So| much| to do, so much      0    4   

  label      loss  max_idx_pos    max_idx_tok  max_idx_tok_value  ...  \
0   0/0  9.976340            0  <|endoftext|>           0.951407  ...   
1   0/1  0.026828            0  <|endoftext|>           0.951336  ...   
2   0/2  2.174434            0  <|endoftext|>           0.809928  ...   
3   0/3  6.801739            0  <|endoftext|>           0.913824  ...   
4   0/4  2.187277            0  <|endoftext|>           0.949831  ...   

  loss_diff   mse_loss explained_variance num_active_features  \
0  0.076798  22.899239           0.251644                  31   
1  0.001894  13.807602           0.169515                  14   
2 -0.015948  10.677010           0.135213                  14   
3  0.016001  10.783960           0.190648                  12   
4 -0.023815  16.349497           0.262152                  18   

                                  top_k_feature_acts  \
0  [25.073442459106445, 20.514616012573242, 15.63...   
1  [35.126258850097656, 33.56575012207031, 23.415...   
2  [60.51701736450195, 39.2960090637207, 14.66763...   
3  [73.247314453125, 38.11686325073242, 23.598638...   
4  [59.24447250366211, 15.890731811523438, 14.734...   

                                      top_k_features  rec_q_max_idx_pos  \
0  [21400, 24519, 24614, 2657, 40680, 38344, 4274...                  0   
1  [44543, 24614, 37365, 21400, 24519, 18012, 475...                  0   
2  [35124, 4387, 4681, 24519, 42590, 23305, 8500,...                  0   
3  [46674, 33541, 24519, 30119, 780, 26242, 45219...                  0   
4  [41111, 24519, 13814, 46507, 7724, 22712, 2006...                  0   

   rec_q_max_idx_tok  rec_q_max_idx_tok_value kl_divergence  
0      <|endoftext|>                 0.998728      0.130836  
1      <|endoftext|>                 0.979545      0.017335  
2      <|endoftext|>                 0.927522      0.076425  
3      <|endoftext|>                 0.953145      0.035008  
4      <|endoftext|>                 0.975143      0.011068  

[5 rows x 25 columns]

In [76]:
pos_mask = (all_token_df.pos.values < 128)
all_token_df = all_token_df[all_token_df.pos < 128]
all_token_features = all_token_features[torch.tensor(pos_mask)]

num_active_features_mask = (all_token_df.num_active_features.values < 100)
all_token_df = all_token_df[all_token_df.num_active_features < 100]
all_token_features = all_token_features[torch.tensor(num_active_features_mask)]

In [77]:
sparsity = (all_token_features > 0).float().mean(dim=0).detach().cpu()
log_sparsity = torch.log10(sparsity)
print((sparsity > 0).float().mean())
print((sparsity > 0).float().sum())

tensor(0.0984)
tensor(4836.)


In [78]:
px.histogram(log_sparsity, nbins=100).show()
px.strip(log_sparsity, hover_data=[[i for i in range(sparse_autoencoder.cfg.d_sae)]]).show()

In [64]:
all_token_df.columns

Index(['str_tokens', 'unique_token', 'context', 'batch', 'pos', 'label',
       'loss', 'max_idx_pos', 'max_idx_tok', 'max_idx_tok_value',
       'top10_token_suppression_diffs', 'top10_token_suppression_inds',
       'top10_token_boosting_vals', 'top10_token_boosting_inds',
       'ablated_loss', 'loss_diff', 'mse_loss', 'explained_variance',
       'num_active_features', 'top_k_feature_acts', 'top_k_features',
       'rec_q_max_idx_pos', 'rec_q_max_idx_tok', 'rec_q_max_idx_tok_value',
       'kl_divergence', 'feature_563', 'feature_210', 'feature_149',
       'feature_983', 'feature_240', 'feature_781', 'feature_52',
       'feature_1004', 'feature_316', 'feature_534', 'feature_399',
       'feature_558', 'feature_737', 'feature_556', 'feature_821',
       'feature_619', 'feature_141', 'feature_115', 'feature_978',
       'feature_413', 'feature_530', 'feature_61', 'feature_241',
       'feature_309', 'feature_378', 'feature_614', 'feature_24519',
       'feature_22818', 'feature_312

In [79]:
px.histogram(all_token_df.num_active_features)

In [100]:
filter_columns = ["str_tokens", "unique_token", "context", "batch", "pos", "label", "loss", "loss_diff", "mse_loss", "num_active_features", "explained_variance", "kl_divergence"]
features = torch.randint(0, sparse_autoencoder.cfg.d_sae, (50,))
# features = torch.tensor([24519,22818,31246])
for feature in features:
    all_token_df[f"feature_{feature}"] = all_token_features[:,feature].detach().cpu()
    mean_activation = (all_token_df[f"feature_{feature}"] > 0).mean()
    if mean_activation > 0.001:
        print(feature.item(), (all_token_df[f"feature_{feature}"] > 0).mean()) # super super dense feature.
        display(all_token_df.sort_values(f"feature_{feature}", ascending=False)[filter_columns + [f"feature_{feature}"]].head(10))
    # else:
        # print(f"feature {feature.item()} is dead")

6148 0.0054039448797622265


str_tokens     unique_token  \
49       arently       arently/49   
103   ultimately   ultimately/103   
16            be            be/16   
117           's           's/117   
97      normally      normally/97   
16            so            so/16   
31            ,"            ,"/31   
35         about         about/35   
125      reasons      reasons/125   
10         least         least/10   

                                               context  batch  pos  label  \
49   er's "Stalag 17"--app|arently| died of natural...      0   49   0/49   
103  , his bosses balked at the idea, but| ultimate...      0  103  0/103   
16   ast was undercooked.\n\nLong believed to| be| ...      0   16   0/16   
117   Gallery\n\nSAN ANTONIO — Whether it|'s| for e...      0  117  0/117   
97   ball Complex in South Bend.\n\nThere are| norm...      0   97   0/97   
16    2 Workshop tools, and some people reckon in d...      0   16   0/16   
31   . Graves, who stared in "Mission: Impossible|,...      0   31   0/31   
35    a law designed to halt prison rape appear to ...      0   35   0/35   
125   Whether it's for economic, medical or persona...      0  125  0/125   
10   JERUSALEM (CNN) -- At| least| three Israeli mi...      0   10   0/10   

         loss  loss_diff   mse_loss  num_active_features  explained_variance  \
49   0.152813  -0.007561  22.461693                   25            0.284598   
103  4.608022   0.005853  35.014313                   25            0.320077   
16   0.216359  -0.001808  28.638283                   30            0.269256   
117  0.475593   0.001076  17.902107                   43            0.254519   
97   9.860717   0.011162  17.802067                   19            0.213012   
16   0.187385  -0.018245  38.025345                   27            0.380660   
31   4.174477  -0.119045  23.074680                   16            0.266260   
35   5.152526  -0.069406  23.940149                   27            0.438832   
125  3.412663   0.194880  24.034176                   21            0.323185   
10   0.362356   0.023093  18.628506                   21            0.255219   

     kl_divergence  feature_6148  
49        1.206683     37.745762  
103       0.707191     10.611686  
16        1.044449      8.011199  
117       0.669992      6.246747  
97        0.212599      6.218996  
16        1.001589      5.099252  
31        0.505384      4.884074  
35        0.266717      2.343852  
125       0.320497      2.284697  
10        0.027539      1.723212

36435 0.006754931099702783


str_tokens unique_token  \
109       hand     hand/109   
110          -        -/110   
7         hand       hand/7   
52      pocket    pocket/52   
74        soft      soft/74   
19        soft      soft/19   
69         ail       ail/69   
20           -         -/20   
34        Soft      Soft/34   
23         lay       lay/23   

                                               context  batch  pos  label  \
109   the most basic, inexpensive personal security...      0  109  0/109   
110   most basic, inexpensive personal security pep...      0  110  0/110   
7    If you've got a mean under|hand| throw or know...      0    7    0/7   
52   , in your car, carried in a purse or| pocket| ...      0   52   0/52   
74    or competition.\n\nMen's and coed| soft|ball ...      0   74   0/74   
19   , and some people reckon in doing so the compa...      0   19   0/19   
69    in Sikkim for the Indian pilgrims visiting K|...      0   69   0/69   
20    and some people reckon in doing so the compan...      0   20   0/20   
34    There's one week left to register for the Adu...      0   34   0/34   
23    night��s game with a steal and a| lay|up.\n\nShe      0   23   0/23   

          loss  loss_diff   mse_loss  num_active_features  explained_variance  \
109   4.580338   0.258321  33.721851                   13            0.280522   
110   2.122732  -0.280678  41.271835                   13            0.239163   
7     4.624420  -0.068542  22.437086                   19            0.292361   
52    3.089430   0.031626  45.505146                   24            0.391933   
74    3.296391   0.621789  23.715321                   24            0.240801   
19   12.638586  -0.039676  32.076668                   14            0.319756   
69    2.581156  -0.085809  33.216606                   15            0.310044   
20    1.204048  -0.039077  34.086033                   16            0.330526   
34    9.698343  -0.080595  17.448347                   36            0.238288   
23    2.171847  -0.004559  39.853867                   19            0.426321   

     kl_divergence  feature_36435  
109       0.439406      72.061020  
110       0.082063      43.389496  
7         0.170253      13.927181  
52        1.411680      10.089045  
74        0.071700       7.521312  
19        0.048425       5.347472  
69        0.059886       5.015781  
20        0.042165       4.916905  
34        0.117768       4.442747  
23        0.016914       4.191241

40307 0.009186706295595785


str_tokens    unique_token  \
5        reating       reating/5   
114      routing     routing/114   
105      seeking     seeking/105   
22       testing      testing/22   
27    collection   collection/27   
27       farming      farming/27   
18      Starting     Starting/18   
109      working     working/109   
108     creation    creation/108   
105      ambling     ambling/105   

                                               context  batch  pos  label  \
5                  The melanoma-t|reating| drug, selum      0    5    0/5   
114   going into effect on 1 August, providing for ...      0  114  0/114   
105   should become a populist party at war with fa...      0  105  0/105   
22    been FDA approved. This advice is currently i...      0   22   0/22   
27   maputra river for the time being as the data| ...      0   27   0/27   
27    from across the continent are gathered to bet...      0   27   0/27   
18    so much to say, so much to cover.| Starting| ...      0   18   0/18   
109   (GFAR). GFAR brings together all those| worki...      0  109  0/109   
108   different."\n\nHammer is Valve's map| creatio...      0  108  0/108   
105   vacationing alone on a secluded beach, r|ambl...      0  105  0/105   

         loss  loss_diff   mse_loss  num_active_features  explained_variance  \
5    3.753883   0.168769  30.676622                   24            0.319123   
114  8.500599   0.320278  21.228973                   15            0.234222   
105  1.318582   0.104259  19.072502                   28            0.204681   
22   3.651146  -0.073051  17.800262                   19            0.209320   
27   5.628787   0.040975  20.446466                   29            0.221912   
27   1.512221   0.177769  11.387548                   23            0.161117   
18   8.342710   0.037370  21.627766                   23            0.277983   
109  4.102480  -0.016284  27.503136                   17            0.292440   
108  5.633252  -0.038354  28.558006                   16            0.294742   
105  4.548299   0.022759  28.394772                   46            0.332884   

     kl_divergence  feature_40307  
5         0.043171      24.011267  
114       0.538304      22.863832  
105       0.165420      22.371901  
22        0.133891      20.942099  
27        0.152496      19.015469  
27        0.106022      18.408773  
18        0.074310      13.428503  
109       0.121848      12.486329  
108       0.058067      11.133650  
105       0.710748      11.108861

34231 0.0027019724398811133


str_tokens unique_token  \
86        June      June/86   
99           a         a/99   
102         15       15/102   
94        July      July/94   
53           ,         ,/53   
96          \n        \n/96   
50         and       and/50   
75          ar        ar/75   
89          \n        \n/89   
90          20        20/90   

                                               context  batch  pos  label  \
86    became a member of the Universal Postal Union...      0   86   0/86   
99    in South Bend.\n\nThere are normally around| ...      0   99   0/99   
102   unsalted butter\n\n10g water\n\n|15|g extra g...      0  102  0/102   
94    on 1 June,[1] and then on 29| July| Vatican C...      0   94   0/94   
53    few days, some a few weeks and for others|,| ...      0   53   0/53   
96   ulated sugar\n\n20g unsalted butter\n|\n|10g w...      0   96   0/96   
50    improvement in a few days, some a few weeks| ...      0   50   0/50   
75    Indian pilgrims visiting Kailash and Manasaro...      0   75   0/75   
89    toasted\n\n50g granulated sugar\n|\n|20g unsa...      0   89   0/89   
90   asted\n\n50g granulated sugar\n\n|20|g unsalte...      0   90   0/90   

         loss  loss_diff   mse_loss  num_active_features  explained_variance  \
86   3.029289   0.030459  64.102020                   35            0.366609   
99   4.691213  -0.111894  23.590702                   19            0.222638   
102  4.260448   0.123243  30.408901                   16            0.209854   
94   2.250494  -0.002539  48.839516                   20            0.355933   
53   1.756900  -0.028621  33.726913                   23            0.374741   
96   0.000201  -0.000003  26.925308                   11            0.218133   
50   2.240136  -0.060578  20.983234                   53            0.278000   
75   1.876564   0.079884  21.166885                   17            0.218260   
89   0.000178  -0.000003  25.890572                   13            0.204186   
90   3.907668  -0.054905  30.458941                   16            0.202514   

     kl_divergence  feature_34231  
86        0.277884       4.511423  
99        0.441428       4.193655  
102       0.970294       3.941461  
94        1.287115       1.978533  
53        0.823476       1.750986  
96        1.431765       1.167138  
50        0.525969       1.008858  
75        0.301355       0.129168  
89        1.374188       0.069876  
90        0.494731       0.062197

7072 0.0029721696838692245


str_tokens unique_token  \
99           "         "/99   
21           "         "/21   
46           "         "/46   
100         !"       !"/100   
35          !"        !"/35   
32           ,         ,/32   
44          .,        .,/44   
8            ]          ]/8   
12           ,         ,/12   
51           )         )/51   

                                               context  batch  pos  label  \
99   \n\nBernthal said he "watches everything|"| an...      0   99   0/99   
21    what the groups called a "torturers tour|"|\n...      0   21   0/21   
46    and Billy Wilder's "Stalag 17|"|--apparently ...      0   46   0/46   
100   he initially turned down the role for "Airpla...      0  100  0/100   
35    stared in "Mission: Impossible," "Airplane|!"...      0   35   0/35   
32    name, Felicia "Snoop" Pearson|,| on The Wire....      0   32   0/32   
44    (he got the gig in Northbrook, Ill|.,| on Aug...      0   44   0/44   
8    "Anybody not reading [Tim Carney|]| regularly ...      0    8    0/8   
12    — So much to do, so much to say|,| so much to...      0   12   0/12   
51   brook, Ill., on Aug. 8, 2006|)| clunking heads...      0   51   0/51   

         loss  loss_diff   mse_loss  num_active_features  explained_variance  \
99   2.276177  -0.079015  25.973282                   21            0.342015   
21   0.111514   0.011836  22.423195                   21            0.245903   
46   1.306789  -0.047929  24.590576                   14            0.309405   
100  0.176026   0.042061  36.392220                   22            0.453622   
35   6.806537   0.208214  20.900173                   13            0.334853   
32   0.836059  -0.016141  25.997372                   24            0.371526   
44   2.141028  -0.005742  11.266057                   24            0.171083   
8    1.138186   0.014272  32.903374                   23            0.388416   
12   1.097434   0.001001  20.116390                   14            0.324269   
51   0.935894   0.020680  29.255789                   36            0.322963   

     kl_divergence  feature_7072  
99        0.391096     34.007156  
21        1.008954     33.385498  
46        0.220100     31.235706  
100       0.610889     21.975542  
35        0.180675     18.301582  
32        0.414617     11.122048  
44        0.081255      7.304327  
8         0.213466      4.194925  
12        0.075505      2.238581  
51        0.659577      1.185847

# Specific Example

In [115]:
prompt = "When John and Mary went to the shops, John gave the bag to"
answer = " Mary"
# prompt = "All's fair in love and"
# answer = " war"
# prompt = " The cat is cute. The dog is"
# prompt = " Alice, with her keen intelligence and artistic talent, discussed philosophy with Bob, who shared her intellect and also possessed remarkable culinary skills, while"
# answer = " cute"
model.reset_hooks()
utils.test_prompt(prompt, answer, model)

HEAD_HOOK_RESULT_NAME = "blocks.10.attn.hook_z"
LAYER_IDX = sparse_autoencoder.cfg.hook_point_layer
HEAD_IDX = 7
def hook_to_ablate_head(head_output: Float[Tensor, "batch seq_len head_idx d_head"], hook: HookPoint, head = (LAYER_IDX, HEAD_IDX)):
    print(hook.layer(), hook.name)
    assert head[0] == hook.layer(), f"{head[0]} != {hook.layer()}"
    assert ("result" in hook.name) or ("q" in hook.name) or ("z" in hook.name)
    head_output[:, :, head[1], :] = 0
    return head_output

with model.hooks(fwd_hooks=[(HEAD_HOOK_RESULT_NAME, hook_to_ablate_head)]):
    utils.test_prompt(prompt, answer, model)

Tokenized prompt: ['<|endoftext|>', 'When', ' John', ' and', ' Mary', ' went', ' to', ' the', ' shops', ',', ' John', ' gave', ' the', ' bag', ' to']
Tokenized answer: [' Mary']


Performance on answer token:
Rank: 0        Logit: 18.19 Prob: 69.93% Token: | Mary|

Top 0th token. Logit: 18.19 Prob: 69.93% Token: | Mary|
Top 1th token. Logit: 15.82 Prob:  6.49% Token: | them|
Top 2th token. Logit: 15.48 Prob:  4.66% Token: | the|
Top 3th token. Logit: 14.93 Prob:  2.66% Token: | his|
Top 4th token. Logit: 14.86 Prob:  2.49% Token: | John|
Top 5th token. Logit: 14.12 Prob:  1.19% Token: | her|
Top 6th token. Logit: 13.99 Prob:  1.04% Token: | their|
Top 7th token. Logit: 13.70 Prob:  0.78% Token: | a|
Top 8th token. Logit: 13.53 Prob:  0.66% Token: | him|
Top 9th token. Logit: 13.39 Prob:  0.57% Token: | Mrs|


Ranks of the answer tokens: [(' Mary', 0)]

Tokenized prompt: ['<|endoftext|>', 'When', ' John', ' and', ' Mary', ' went', ' to', ' the', ' shops', ',', ' John', ' gave', ' the', ' bag', ' to']
Tokenized answer: [' Mary']
10 blocks.10.attn.hook_z


Performance on answer token:
Rank: 0        Logit: 19.21 Prob: 86.60% Token: | Mary|

Top 0th token. Logit: 19.21 Prob: 86.60% Token: | Mary|
Top 1th token. Logit: 15.60 Prob:  2.36% Token: | them|
Top 2th token. Logit: 15.57 Prob:  2.29% Token: | the|
Top 3th token. Logit: 15.03 Prob:  1.33% Token: | his|
Top 4th token. Logit: 14.56 Prob:  0.83% Token: | John|
Top 5th token. Logit: 14.16 Prob:  0.56% Token: | her|
Top 6th token. Logit: 14.07 Prob:  0.51% Token: | their|
Top 7th token. Logit: 13.91 Prob:  0.43% Token: | Mrs|
Top 8th token. Logit: 13.87 Prob:  0.42% Token: | a|
Top 9th token. Logit: 13.33 Prob:  0.24% Token: | him|


Ranks of the answer tokens: [(' Mary', 0)]

In [125]:
token_df, original_cache, cache_reconstructed_query, feature_acts = eval_prompt([prompt + answer], model, sparse_autoencoder, head_idx_override=7)
print(token_df.columns)
filter_cols = ["str_tokens", "unique_token", "context", "batch", "pos", "label", "loss", "loss_diff", "mse_loss", "num_active_features", "explained_variance", "kl_divergence"]
token_df[filter_cols].style.background_gradient(
    subset=["loss_diff", "mse_loss","explained_variance", "num_active_features", "kl_divergence"],
    cmap="coolwarm")


Index(['str_tokens', 'unique_token', 'context', 'batch', 'pos', 'label', 'loss', 'max_idx_pos', 'max_idx_tok', 'max_idx_tok_value', 'top10_token_suppression_diffs', 'top10_token_suppression_inds', 'top10_token_boosting_vals', 'top10_token_boosting_inds', 'ablated_loss', 'loss_diff', 'mse_loss', 'explained_variance', 'num_active_features', 'top_k_feature_acts', 'top_k_features', 'rec_q_max_idx_pos', 'rec_q_max_idx_tok', 'rec_q_max_idx_tok_value', 'kl_divergence'], dtype='object')


In [133]:
def plot_attn(patterns, token_df, title="", facet_col_labels = ["Original", "Reconstructed"]):
    '''
    # patterns_original = cache[utils.get_act_name("pattern", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
    # patterns_reconstructed = cache_reconstructed_query[utils.get_act_name("pattern", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
    patterns_original = cache[utils.get_act_name("attn_scores", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
    patterns_reconstructed = cache_reconstructed_query[utils.get_act_name("attn_scores", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
    both_patterns = torch.stack([patterns_original, patterns_reconstructed])
    plot_attn(both_patterns.detach().cpu(), token_df, title="Original and Reconstructed Attention Distribution")
    
    '''
    fig = px.imshow(patterns, text_auto=".2f", title=title,
                    facet_col=0,
                    color_continuous_midpoint=0,
                    color_continuous_scale="RdBu",
                    )
    
    tickvals = 1+ np.arange(patterns.shape[2])
    ticktext = token_df["unique_token"].tolist()
    
    # add tokens as x-ticks and y-ticks, for each facet
    # Update x-ticks and y-ticks for each facet
    for i in range(len(facet_col_labels)):
        fig.update_xaxes(
            dict(tickmode='array', tickvals=tickvals, ticktext=ticktext),
            row=1, col=i+1
        )
        fig.update_yaxes(
            dict(tickmode='array', tickvals=tickvals, ticktext=ticktext),
            row=1, col=i+1
        )
    
    
    # add facet col labels:
    for i, label in enumerate(facet_col_labels):
        fig.layout.annotations[i].text = label
        fig.layout.annotations[i].font.size = 20
        
    fig.update_layout(
        width=1200,
        height=800,
    )
    fig.show()


patterns_original = original_cache[utils.get_act_name("attn_scores", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
patterns_reconstructed = cache_reconstructed_query[utils.get_act_name("attn_scores", LAYER_IDX)][0,HEAD_IDX].detach().cpu()
both_patterns = torch.stack([patterns_original, patterns_reconstructed])
plot_attn(both_patterns.detach().cpu(), token_df, title="Original and Reconstructed Attention Distribution")

In [137]:
POS_INTEREST = feature_acts.shape[0] - 2 # index from 0.

# reload(joseph.visualisation)
# from joseph.visualisation import *

print(token_df["unique_token"][POS_INTEREST]) # bos gone.
plot_line_with_top_10_labels(feature_acts[POS_INTEREST], "", 10)

vals, inds = torch.topk(feature_acts[POS_INTEREST],10)

print(inds)
# plot_attn_score_by_feature(model, sparse_autoencoder, inds, original_cache, token_df, pos_interest=POS_INTEREST, vals = vals)
# plot_unembed_score_by_feature(model, sparse_autoencoder, inds, token_df, vals=vals)

 to/13


tensor([33416, 40148, 39178,  3198,  3403, 46531,  1504, 24295, 34686,  5872],
       device='mps:0')


In [138]:

filter_columns = ["str_tokens", "unique_token", "context", "batch", "pos", "label", "loss", "loss_diff", "mse_loss", "num_active_features", "explained_variance", "kl_divergence"]
# features = torch.tensor([24519,22818,31246])
for feature in inds:
    all_token_df[f"feature_{feature}"] = all_token_features[:,feature].detach().cpu()
    mean_activation = (all_token_df[f"feature_{feature}"] > 0).mean()
    if mean_activation > 0.001:
        print(feature.item(), (all_token_df[f"feature_{feature}"] > 0).mean()) # super super dense feature.
        display(all_token_df.sort_values(f"feature_{feature}", ascending=False)[filter_columns + [f"feature_{feature}"]].head(30))
    # else:
        # print(f"feature {feature.item()} is dead")

33416 0.015671440151310456


str_tokens     unique_token                                                                                                        context  batch  pos  label       loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_33416
108         upon         upon/108                      �s achieved.�� These words were bestowed| upon| departing Liverpool legend Steven Gerrard      0  108  0/108   1.827929  -0.025412  26.296909                   13            0.294253       0.177387      36.212723
118           of           of/118                                       to a lack of money. This was incredibly thoughtful| of| our SS as we are      0  118  0/118   4.574773  -0.026509  35.341320                   16            0.448614       0.531646      34.090366
104       toward       toward/104                             so many voters, including many Democrats, now feel| toward| the former First Lady.      0  104  0/104   1.411798  -0.019673  35.153828                   21            0.376786       0.226366      23.605068
94     supported     supported/94                                     from a desire to give back to a community that| supported| their family��s      0   94   0/94   4.840488  -0.099084  20.955315                   20            0.246395       0.337279      23.406496
50          made          made/50                   a handwritten note inside made this a personal experience that| made| my wife and I remember      0   50   0/50   4.799685   0.060308  24.014328                   11            0.264542       0.244079      23.103096
90           and           and/90                                                  -hundred dollar bill (which made my wife| and| I tear up). We      0   90   0/90   1.300161  -0.104232  33.309311                   16            0.338397       0.273260      22.365831
108         knew         knew/108                                   choice for MVP of the league by people who already| knew| the answer was Nne      0  108  0/108   0.979763   0.041352  25.839870                   13            0.288399       0.344854      21.209351
61            to            to/61                                   my wife and I remember just how important it is| to| give not just this time      0   61   0/61   0.296795   0.006644  31.767050                   17            0.293035       0.764488      21.104010
60          know          know/60                                           \n��I think people all over the world| know| that Gerrard has been a      0   60   0/60   3.410050   0.040935  14.461056                   20            0.214603       0.204393      19.109781
53           and           and/53                   inside made this a personal experience that made my wife| and| I remember just how important      0   53   0/53   1.370909  -0.089357  26.194069                   14            0.265094       0.082880      16.015982
109   overlooked   overlooked/109                   ukkah that the Cuban authorities have once again| overlooked| an opportunity to release Alan      0  109  0/109  10.619183  -0.141586  29.552469                   16            0.340881       0.241465      13.909817
113      release      release/113   the Cuban authorities have once again overlooked an opportunity to| release| Alan on humanitarian grounds is      0  113  0/113   3.480469   0.081523  48.109608                   20            0.367305       0.254667      13.292278
35       inspire       inspire/35                                              Jane��s portrayal of the Punisher helped| inspire| Jon Bernthal��      0   35   0/35   4.767493   0.083506  22.061604                   29            0.270129       0.355769      12.235095
98     including     including/98                          only feed the deep distrust that so many voters,| including| many Democrats, now feel      0   98   0/98   1.928390  -0.080196  25.200394                   18            0.254551       0.309892  

40148 0.024317751958930017


str_tokens    unique_token                                                                                                        context  batch  pos  label       loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_40148
67           of           of/67                   -old woman -- were arrested Saturday outside the home| of| former Vice President Dick Cheney      0   67   0/67   0.097505   0.000199  58.667740                   25            0.418904       0.779530      43.990654
80           of           of/80                          son was born in Baltimore, Maryland, the daughter| of| two incarcerated drug addicts,      0   80   0/80   0.002993  -0.000193  34.380875                   18            0.324549       0.318383      40.442352
8         after         after/8                         Caltech will rename its medical engineering department| after| receiving a $30 million      0    8    0/8   2.359654  -0.036089  16.508102                   19            0.214003       0.056215      37.777534
9            of            of/9                                        1929 Vatican City postage stamp featuring the image| of| Pope Pius XI\n      0    9    0/9   0.108239  -0.002658  16.032003                   24            0.208984       0.057035      34.135803
111          by          by/111                                from the beginning. The first Panda Inn was started| by| Andrew and his father,      0  111  0/111   1.262677   0.020289  25.325024                   40            0.233587       0.620082      29.243307
30           of           of/30                                            short.\n\nThomas Jane��s portrayal| of| the Punisher helped inspire      0   30   0/30   0.048434  -0.000151  29.194836                   19            0.314965       0.439080      29.075880
117        than        than/117                  bestowed upon departing Liverpool legend Steven Gerrard by none other| than| Francesco Totti,      0  117  0/117   0.017944  -0.000788  46.635860                   24            0.384581       0.762664      28.893013
51      killing      killing/51                               \nOne of those rockets struck near a college,| killing| one person, according to      0   51   0/51   1.935329   0.168647  30.452702                   10            0.315505       0.165659      28.258486
9       release       release/9                                                     (JTA) — Cuba said it will| release| nearly 3,000 prisoners      0    9    0/9   5.431316  -0.020325  28.655313                   23            0.280147       0.449499      26.257072
89      injured      injured/89                            killed people.\n\nThe strike at the ministry| injured| several people, according to      0   89   0/89   8.031948   0.170121  29.352589                   17            0.300335       0.111514      23.344112
92         with         with/92              , Food Tank is also excited to announce our collaboration| with| the Global Forum on Agricultural      0   92   0/92   0.061226  -0.001408  16.131134                   23            0.189431       0.068503      21.006083
16       played       played/16                                         18, 1980) is an American actress. She| played| a character of the same      0   16   0/16   4.759113   0.037716  25.641628                   20            0.235075       0.020016      20.658804
69           by           by/69   Vatican post office began operating with supplies and equipment donated| by| the Italian government. Vatican      0   69   0/69   0.286478  -0.004363  25.980350                   34            0.289465       0.208936      20.184460
15         from         from/15               medical engineering department after receiving a $30 million gift| from| Andrew and Peggy Cherng      0   15   0/15   0.224501   0.000181  25.192493                   18            0.226897       0.045053      19.850430
44        wrote

39178 0.03323426101053769


...

str_tokens  unique_token                                                                                                        context  batch  pos  label      loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_24295
9            of          of/9                                        1929 Vatican City postage stamp featuring the image| of| Pope Pius XI\n      0    9    0/9  0.108239  -0.002658  16.032003                   24            0.208984       0.057035      26.411705
7           the         the/7                                             1929 Vatican City postage stamp featuring| the| image of Pope Pius      0    7    0/7  1.662392  -0.078042  14.816973                   16            0.188894       0.241311      15.601090
11            P          P/11                                     29 Vatican City postage stamp featuring the image of Pope| P|ius XI\n\nThe      0   11   0/11  2.060232   0.002631  32.820930                   14            0.287693       0.154371      14.872159
45        after      after/45                    \n\nThe postal history of Vatican City begins shortly| after| its official foundation on 11      0   45   0/45  0.253191  -0.001308  18.003279                   16            0.231121       0.239284      13.341515
58          the        the/58                      foundation on 11 February 1929. Two days later,| the| Vatican post office began operating      0   58   0/58  1.234375   0.062256  36.123386                   19            0.390998       0.660773      11.706806
6     featuring   featuring/6                                                1929 Vatican City postage stamp| featuring| the image of Pope P      0    6    0/6  6.571790  -0.038542  19.034027                   20            0.226424       0.042419       9.922002
67     visiting   visiting/67                                           La pass in Sikkim for the Indian pilgrims| visiting| Kailash and Man      0   67   0/67  4.216156  -0.024530  21.343388                   23            0.216691       0.383867       7.683740
69           by         by/69   Vatican post office began operating with supplies and equipment donated| by| the Italian government. Vatican      0   69   0/69  0.286478  -0.004363  25.980350                   34            0.289465       0.208936       6.833577
57            ,          ,/57                       official foundation on 11 February 1929. Two days later|,| the Vatican post office began      0   57   0/57  0.587478  -0.010605  20.762032                   17            0.293326       0.327724       6.636838
70          the        the/70      post office began operating with supplies and equipment donated by| the| Italian government. Vatican City      0   70   0/70  0.922197  -0.055542  19.717548                   25            0.231680       0.173264       6.288260
13           XI         XI/13                                   City postage stamp featuring the image of Pope Pius| XI|\n\nThe Vatican post      0   13   0/13  2.471250   0.002036  18.818083                   25            0.181546       0.252592       5.041267
49           on         on/49                history of Vatican City begins shortly after its official foundation| on| 11 February 1929. Two      0   49   0/49  2.709486  -0.003576  18.375710                   20            0.163122       0.086109       5.017296
16          The        The/16                                  featuring the image of Pope Pius XI\n\n|The| Vatican post office has operated      0   16   0/16  2.334086   0.092524  41.327248                   22            0.412167       1.108112       4.374084
10         Pope       Pope/10                                      1929 Vatican City postage stamp featuring the image of| Pope| Pius XI\n\n      0   10   0/10  1.731955   0.180618  23.811659                   29            0.273740       0.293803       4.203840
47     official   official/47          The postal history of

34686 0.03728721967035936


str_tokens   unique_token                                                                                                          context  batch  pos  label       loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_34686
106    together   together/106                          on Agricultural Research (GFAR). GFAR brings| together| all those working to strengthen      0  106  0/106   0.031311   0.001357  20.597385                   26            0.194236       0.215760      25.007917
100          of         of/100                       particularly good about preventive health care; not even half| of| all people over the age      0  100  0/100   0.562866   0.021255  17.452072                   17            0.223537       0.058999      23.479309
58          for         for/58   of preventive health care services like cancer screening, especially| for| elderly people in aging populations      0   58   0/58   1.512048   0.096958  12.840855                   21            0.127978       0.062142      23.164785
101         all        all/101                                 good about preventive health care; not even half of| all| people over the age of      0  101  0/101   2.031934  -0.177231  19.742846                   18            0.218556       0.238562      22.758362
69           by          by/69     Vatican post office began operating with supplies and equipment donated| by| the Italian government. Vatican      0   69   0/69   0.286478  -0.004363  25.980350                   34            0.289465       0.208936      20.810282
98    including   including/98                            only feed the deep distrust that so many voters,| including| many Democrats, now feel      0   98   0/98   1.928390  -0.080196  25.200394                   18            0.254551       0.309892      19.935429
79           of          of/79                                     it did not already control and creates a sales force| of| about 3,000 people      0   79   0/79   1.530405   0.028926  18.907993                   20            0.281812       0.384424      19.522770
85    reminding   reminding/85                                    associated with the team's hilltop perch,| reminding| us that before the land      0   85   0/85   9.352238  -0.085811  31.259647                   17            0.347669       0.220206      17.155725
9           for          for/9                                      Preventive health care is a powerful tool| for| keeping medical costs down.      0    9    0/9   1.046641   0.043708  23.139496                   25            0.264769       0.101179      16.840492
113     release    release/113     the Cuban authorities have once again overlooked an opportunity to| release| Alan on humanitarian grounds is      0  113  0/113   3.480469   0.081523  48.109608                   20            0.367305       0.254667      16.801311
79       killed      killed/79                            a near daily occurrence but have only occasionally injured or| killed| people.\n\nThe      0   79   0/79   0.467311   0.052787  28.982018                   21            0.268105       0.508917      15.067172
66     deceived    deceived/66                         \nBut her recent health scare, in which she| deceived| virtually everyone about the real      0   66   0/66  13.258922  -0.072919  19.080076                   23            0.246605       0.156798      15.055356
7           and          and/7                                 Farmers and farmers groups, researchers| and| scientists, and government leaders      0    7    0/7   0.613498  -0.031848  12.398635                   18            0.124057       0.162656      14.517052
104          by         by/104                                  ler was asked his choice for MVP of the league| by| people who already knew the      0  104  0/104   4.242134   0.014342  10.669092                   19            0.144557       0.220938      14.471134


5872 0.006754931099702783


str_tokens unique_token                                                                                           context  batch  pos  label       loss  loss_diff   mse_loss  num_active_features  explained_variance  kl_divergence  feature_5872
56        when      when/56                           baseline, so she could finish a fast break,| when| her team led by only      0   56   0/56   5.545222   0.029348  13.030224                   15            0.193100       0.118093      8.391265
26          in        in/26              according to law enforcement sources. Graves, who stared| in| "Mission: Impossible,"      0   26   0/26   3.936189  -0.141316  37.555878                   23            0.347614       0.595677      7.159115
25      stared    stared/25              , according to law enforcement sources. Graves, who| stared| in "Mission: Impossible      0   25   0/25  13.513718  -0.070458  30.535774                   20            0.371663       0.033607      6.920449
48          so        so/48                           simple rim-run, from baseline to baseline,| so| she could finish a fast      0   48   0/48   6.020428  -0.033440  14.951773                   25            0.226019       0.362099      5.351781
89        wife      wife/89                                     one-hundred dollar bill (which made my| wife| and I tear up).      0   89   0/89   2.130591  -0.022562  51.316654                   21            0.403981       1.558514      4.413623
86          as        as/86               not limited to): rise in blood pressure, feeling| as| though your brain may explode      0   86   0/86   4.417199  -0.147423  27.422178                   15            0.248521       0.263050      4.186804
27          my        my/27                                the box on my porch. The thoughtfulness of| my| SS and their SO is      0   27   0/27   1.925600  -0.116406  39.358383                   20            0.435122       0.785312      3.760057
50       could     could/50                              -run, from baseline to baseline, so she| could| finish a fast break,      0   50   0/50   0.828099   0.008622  12.161452                   21            0.141774       0.120024      3.057271
90         and       and/90                                     -hundred dollar bill (which made my wife| and| I tear up). We      0   90   0/90   1.300161  -0.104232  33.309311                   16            0.338397       0.273260      2.640450
55           ,         ,/55                             to baseline, so she could finish a fast break|,| when her team led by      0   55   0/55   3.274050  -0.028076  13.485497                   27            0.201120       0.392348      2.508426
56        just      just/56              a personal experience that made my wife and I remember| just| how important it is to      0   56   0/56   5.490949   0.030488  17.679199                   22            0.194055       0.043808      1.434138
53         and       and/53      inside made this a personal experience that made my wife| and| I remember just how important      0   53   0/53   1.370909  -0.089357  26.194069                   14            0.265094       0.082880      0.965726
17           .         ./17                                   , so much to say, so much to cover|.| Starting with this: Roger      0   17   0/17   0.887217  -0.004798  17.565090                   13            0.246400       0.070646      0.930655
57         her       her/57                               , so she could finish a fast break, when| her| team led by only one      0   57   0/57   3.154233   0.004278  14.098950                   13            0.189106       0.123062      0.854221
64           .         ./64                                  break, when her team led by only one point|.|\n\nThe Sparks beat      0   64   0/64   0.425541  -0.004984  11.309422                   12            0.175295       0.079231      0.803804
125        and      and/125         